In [78]:
import numpy as np
import pandas as pd
import networkx as nx
import plotly.graph_objects as go
from matplotlib import pyplot as plt

In [79]:
country_codes = pd.read_csv("./Datasets/BACI_HS92_V202401/country_codes_V202401.csv")
product_codes = pd.read_csv("./Datasets/BACI_HS92_V202401/product_codes_HS92_V202401.csv")
data_2022 = pd.read_csv("./Datasets/BACI_HS92_V202401/BACI_HS92_Y2022_V202401.csv")

In [80]:
print(data_2022.head())
print(data_2022.info())

      t  i   j       k       v              q
0  2022  4  20  210610   0.392          0.002
1  2022  4  20  210690   0.068          0.001
2  2022  4  20  271000   6.233          8.103
3  2022  4  20  843131   0.352          0.022
4  2022  4  24   71332  35.025         25.060
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10830582 entries, 0 to 10830581
Data columns (total 6 columns):
 #   Column  Dtype  
---  ------  -----  
 0   t       int64  
 1   i       int64  
 2   j       int64  
 3   k       int64  
 4   v       float64
 5   q       object 
dtypes: float64(1), int64(4), object(1)
memory usage: 495.8+ MB
None


In [81]:
G = nx.from_pandas_edgelist(data_2022, source='i', target='j', edge_attr=['k', 'v', 'q'], create_using=nx.DiGraph())

In [82]:
# country_codes.set_index("country_code", drop=True, inplace=True)
country_codes.drop(["country_name","country_iso2"], axis="columns", inplace=True)

In [83]:
country_dict = dict(country_codes.values)

G = nx.relabel_nodes(G, country_dict)

In [84]:
pos = nx.spring_layout(G) # Define the layout for node positioning
# nx.draw(G, pos, with_labels=True, node_size=300, node_color='skyblue', font_size=10, font_color='black')
# plt.show()

In [85]:
pos = nx.spring_layout(G)
node_x = [x for x, y in pos.values()]
node_y = [-y for x, y in pos.values()]

edge_x = [x for n0, n1 in G.edges for x in (pos[n0][0], pos[n1][0], None)]
edge_y = [y for n0, n1 in G.edges for y in (-pos[n0][1], -pos[n1][1], None)]

In [86]:
edge_trace = go.Scatter(
    x=edge_x, y=edge_y,
    line=dict(width=0.5, color='#888'),
    hoverinfo='none',
    mode='lines')

node_trace = go.Scatter(
    x=node_x, y=node_y,
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        # colorscale options
        #'Greys' | 'YlGnBu' | 'Greens' | 'YlOrRd' | 'Bluered' | 'RdBu' |
        #'Reds' | 'Blues' | 'Picnic' | 'Rainbow' | 'Portland' | 'Jet' |
        #'Hot' | 'Blackbody' | 'Earth' | 'Electric' | 'Viridis' |
        colorscale='YlGnBu',
        reversescale=True,
        color=[],
        size=10,
        colorbar=dict(
            thickness=15,
            title='Node Connections',
            xanchor='left',
            titleside='right'
        ),
        line_width=2))

node_adjacencies = []
node_text = []
for node, adjacencies in enumerate(G.adjacency()):
    node_adjacencies.append(len(adjacencies[1]))
    node_text.append('# of connections: '+str(len(adjacencies[1])))

node_trace.marker.color = node_adjacencies
node_trace.text = node_text

fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20,l=5,r=5,t=40),
                xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                )
fig.show()

Csomópont alapú mutatók, amely a vizsgálat során használatra kerülnek:

- Csomópont aszimmetria (Node Asymmentry): Azt méri, hogy egy adott csomópont a
hálózaton belül mennyire hasonlít más csomópontokra azáltal, hogy összehasonlítja a
csomópont tulajdonságait az átlagos tulajdonságokkal.
- Köztességi centralitás (Betwennes Centrality): Azt méri, hogy egy adott csomópont
mennyire fontos a hálózatban a különböző közvetítő szerepei miatt. A közvetítő szerep
azt jelenti, hogy egy adott információ milyen gyorsan jut el (milyen rövid úton ér el)
egy másik csomóponthoz.
- Legrövidebb Utak (Shortest Paths): A leggyorsabb, vagyis a legrövidebb út hosszát
méri, amelyen egy csomópont elérheti egy másik csomópontot a hálózatban.
- Harmonikus Centralitás (Harmonic Centrality): Azt méri, hogy egy adott csomópont
mennyire központi szerepű a hálózatban azáltal, hogy az összes többi csomóponthoz
mérten mennyi időbe telik eljutni az adott csomópontra.
- Sajátvektor centralitás (Eigenvector Centrality): Azt méri, hogy mennyire fontos egy
adott csomópont a hálózatban, figyelembe véve azon csomópontok fontosságát,
amelyekkel a csomópont közvetlenül kapcsolódik. Az sajátvektor centralitás azoknak
a csomópontoknak ad magas értéket, amelyek magas fontossággal rendelkeznek, és
amelyekkel sok más fontos csomópont van kapcsolatban.
- Csomópont Magasság (Node Coreness): Azt méri, hogy egy adott csomópont
mennyire kapcsolódik közvetlenül a hálózat legfontosabb csomópontjaival, vagyis a
magas csomópontmaggal rendelkező csomópontokkal.

Hálózat-szintű mutatók:


- Skála független hatás (Scale Free Property): Azt méri, hogy a hálózat mennyire követi
a skála-független tulajdonságokat. Ez azt jelenti, hogy a hálózatban található
csomópontok száma egyre több csomóponthoz kapcsolódik, kialakítva a stabilitást a
nagy mértékű robusztusságon keresztül, vagyis a kereskedelmi biztonságot mutatja
meg a hatékony összeköttetés fenntartásával (De Benedictis L. &., 2011).
- Asszortativitás (Assortativiy): Azt méri, hogy a hálózatban található csomópontok
mennyire kapcsolódnak azonos vagy eltérő tulajdonságokkal rendelkező
csomópontokhoz.
- Összakapcsoltság (Connectivity): Azt méri, hogy a hálózatban található csomópontok
mennyire és hogyan összekapcsolódnak egymáshoz.
- Klaszterezettség (Clustering) : Azt méri, hogy mennyire összetett a hálózat, vagyis,
hogy a csomópontok csoportokba rendeződnek-e a hálózaton belül. A magas
klaszterezettség azt jelenti, hogy a hálózatban található csomópontok nagyobb
valószínűséggel kapcsolódnak egymáshoz, mint más csoportokban találhatóakhoz.
- Reziliencia/Rugalmasság (Resilience): Azt méri, hogy a hálózat mennyire ellenálló a
változásokkal szemben. A magas reziliencia azt jelenti, hogy a hálózat képes ellenállni
a zavaroknak, mint a csomópontok kiesésének vagy a hálózat struktúrájának
változásának. Fordított esetben pedig mennyire nem ellenálló a zavarokkal szemben.
- Robusztusság (Robustness): Azt méri, hogy a hálózatban található csomópontok
mennyire kapcsolódnak egymáshoz, vagyis mennyire képeznek csoportokat.
10
- Centralizáció (Centralization): A csomópontok (vagy csomópontok csoportjai)
fontosságát méri a hálózatban. A centralitás értéke azt mutatja meg, hogy mennyire
fontos vagy befolyásos egy adott csomópont a hálózatban.
- Magasságrend/ magassági fokszám (Coreness): Azt méri, hogy a hálózatban található
csomópontok mennyire kapcsolódnak a magas csomópontmaggal rendelkező
csomópontokkal.
- Aszimmetria (Assimetry): Azt jelenti, hogy a hálózatban lévő csomópontok vagy
kapcsolatok nem egyenlőek vagy nem szimmetrikusak. Két fajtát különböztetünk
meg: bilaterális (kétoldalú) vagy multilaterális.
o Bilaterális: két csomópont közötti kapcsolat irányított, és az egyik
csomópontnak van egy másik csomóponttal való kapcsolata, míg a másik
csomópontnak nincs.
o Multilaterális: két csomópont közötti kapcsolat több irányba is mutat, és az
egyik csomópontnak van egy másik csomóponttal való kapcsolata, míg a másik
csomópontnak is van egy másik csomóponttal való kapcsolata.
- Reciprocitás/Kölcsönösség (Reciprocity): Azt mutatja meg, hogy a kapcsolatok
mennyire kölcsönösek a hálózatban. Magas reciprocitás esetén a kapcsolatok jelentős
része kölcsönös, míg alacsony reciprocitás esetén a kapcsolatok többsége pedig
irányított. Másképp kifejezve, a hálózati kölcsönösség a hálózati struktúrákon
keresztül történő együttműködés fokozására utal. Ez kétféleképpen értelmezhető: a
fontos pozíciókat betöltő alanyok együttműködőbbek, mint mások (Molesti, 2017)
és/vagy az alanyok kooperatív klasztereket alkotnak, hogy elkerüljék a dezertálók
behatolását (Melamed, 2018).
